## Description
In this part of the project, we will use supervised learning algorithms, namely, Decision Trees/Random Forests, SVM, and Logistic Regression algorithms to predict disease type given gene expression data.

## Import Packages

In [35]:
import pandas as pd
import numpy as np
import math
from sklearn.tree import DecisionTreeClassifier # Import Decision Tree Classifier
from sklearn.tree import plot_tree
# from sklearn.tree.export import export_text
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split # Import train_test_split function
from sklearn import metrics #Import scikit-learn metrics module for accuracy calculation
from sklearn.model_selection import KFold # import KFold

In [3]:
#Settings
pd.set_option('display.max_rows', 100)
pd.set_option('display.max_columns', 100)

## Load in Data (Run this cell only once - large file)

In [4]:
data = pd.read_csv("combinedFPKM.csv")
data

//anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3051: DtypeWarning: Columns (0) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


5ce879cb-fe9c-5cb9-9b2f-54779d6ad6c4  Cancer  ENSG00000000003.13  \
0                                     NaN  Brease            9.342228   
1                                     NaN  Brease           19.658110   
2                                     NaN  Brease            1.028690   
3                                     NaN  Brease           14.286209   
4                                     NaN  Brease           26.223014   
...                                   ...     ...                 ...   
6724                                  NaN  Kidney           16.863419   
6725                                  NaN  Kidney            6.163899   
6726                                  NaN  Kidney            8.674678   
6727                                  NaN  Kidney           34.396800   
6728                                         NaN                 NaN   

      ENSG00000000005.5  ENSG00000000419.11  ENSG00000000457.12  \
0              0.828756           19.959239            3.713461   
1              0.000000           34.302484            4.674391   
2              0.098894          129.116200            3.580859   
3              0.000000           26.467142            9.394148   
4              0.435370           32.506914            4.689478   
...                 ...                 ...                 ...   
6724           1.190972           25.036156            1.546225   
6725           0.148058           19.183121            0.750365   
6726           0.114501           19.381643            2.343508   
6727           0.055600           36.833200            3.158000   
6728                NaN                 NaN                 NaN   

      ENSG00000000460.15  ENSG00000000938.11  ENSG00000000971.14  \
0               1.577598            1.557466            3.895561   
1               3.941016            1.505171            2.325878   
2               1.491591            0.316237            1.213933   
3               2.610714            1.062695            4.011221   
4               2.860832            3.011771            7.098766   
...                  ...                 ...                 ...   
6724            0.530593            0.380801            0.198917   
6725            0.237029            1.024673            0.316076   
6726            0.775450            6.802906            4.488155   
6727            3.425500            0.261800            1.700400   
6728                 NaN                 NaN                 NaN   

      ENSG00000001036.12  ENSG00000001084.9  ENSG00000001167.13  \
0              25.113650           8.062482           19.397789   
1              47.765837           2.832710           13.435799   
2              16.241104           4.633766           14.292499   
3              13.538960           8.880911           20.320788   
4              14.828362           8.059247           15.627057   
...                  ...                ...                 ...   
6724           21.910257           7.111496            3.217752   
6725           14.275677           3.175311            3.335938   
6726           25.952476           5.249633            7.294552   
6727           11.615200           2.212600           14.548800   
6728                 NaN                NaN                 NaN   

      ENSG00000001460.16  ENSG00000001461.15  ENSG00000001497.15  \
0               0.745033            5.288839           16.220930   
1               1.060891            2.509758           15.209583   
2               1.556456            8.963247           10.047671   
3               2.266629            7.531598            9.140765   
4               1.870120            4.607655           11.168068   
...                  ...                 ...                 ...   
6724            0.504725            5.999998           11.247115   
6725            0.263273            3.251318           10.133759   
6726            1.061333            5.843669            6.966201   
6727            1.837

## Preprocessing

In [5]:
dataset = data.iloc[0:6728,1:60485]
dataset = dataset.rename(columns = {'Cancer': 'CancerType'})
dataset.loc[dataset.CancerType == 'Brease', 'CancerType'] = 'Breast'
dataset.loc[dataset.CancerType == 'Hema', 'CancerType'] = 'Blood'
dataset.loc[dataset.CancerType == 'Bronchus', 'CancerType'] = 'Lung'
dataset

CancerType  ENSG00000000003.13  ENSG00000000005.5  ENSG00000000419.11  \
0        Breast            9.342228           0.828756           19.959239   
1        Breast           19.658110           0.000000           34.302484   
2        Breast            1.028690           0.098894          129.116200   
3        Breast           14.286209           0.000000           26.467142   
4        Breast           26.223014           0.435370           32.506914   
...         ...                 ...                ...                 ...   
6723     Kidney            6.948603           0.121193           16.974004   
6724     Kidney           16.863419           1.190972           25.036156   
6725     Kidney            6.163899           0.148058           19.183121   
6726     Kidney            8.674678           0.114501           19.381643   
6727     Kidney           34.396800           0.055600           36.833200   

      ENSG00000000457.12  ENSG00000000460.15  ENSG00000000938.11  \
0               3.713461            1.577598            1.557466   
1               4.674391            3.941016            1.505171   
2               3.580859            1.491591            0.316237   
3               9.394148            2.610714            1.062695   
4               4.689478            2.860832            3.011771   
...                  ...                 ...                 ...   
6723            1.690258            0.465973            3.025936   
6724            1.546225            0.530593            0.380801   
6725            0.750365            0.237029            1.024673   
6726            2.343508            0.775450            6.802906   
6727            3.158000            3.425500            0.261800   

      ENSG00000000971.14  ENSG00000001036.12  ENSG00000001084.9  \
0               3.895561           25.113650           8.062482   
1               2.325878           47.765837           2.832710   
2               1.213933           16.241104           4.633766   
3               4.011221           13.538960           8.880911   
4               7.098766           14.828362           8.059247   
...                  ...                 ...                ...   
6723            0.724664           31.996083           3.956931   
6724            0.198917           21.910257           7.111496   
6725            0.316076           14.275677           3.175311   
6726            4.488155           25.952476           5.249633   
6727            1.700400           11.615200           2.212600   

      ENSG00000001167.13  ENSG00000001460.16  ENSG00000001461.15  \
0              19.397789            0.745033            5.288839   
1              13.435799            1.060891            2.509758   
2              14.292499            1.556456            8.963247   
3              20.320788            2.266629            7.531598   
4              15.627057            1.870120            4.607655   
...                  ...                 ...                 ...   
6723            8.115076            2.550479            5.609914   
6724            3.217752            0.504725            5.999998   
6725            3.335938            0.263273            3.251318   
6726            7.294552            1.061333            5.843669   
6727           14.548800            1.837500            1.996000   

      ENSG00000001497.15  ENSG00000001561.6  ENSG00000001617.10  \
0              16.220930           5.519227           37.908338   
1              15.209583          12.459083           24.168524   
2              10.047671          14.436147           57.131994   
3               9.140765          12.365308           17.293903   
4              11.168068           0.931820            7.327714   
...                  ...                ...                 ...   
6723            9.413006           4.735368           24.101956   
6724           11.247115          16.586646           46.095228   
6725           10.133759  

In [6]:
check = dataset.iloc[:,0]
check_np = check.to_numpy()
print(check)
print(np.unique(check_np))

0       Breast
1       Breast
2       Breast
3       Breast
4       Breast
         ...  
6723    Kidney
6724    Kidney
6725    Kidney
6726    Kidney
6727    Kidney
Name: CancerType, Length: 6728, dtype: object
['Blood' 'Breast' 'Kidney' 'Lung']


## Decision Tree Model

In [120]:
#Shuffle Dataset
dataset = dataset.sample(frac=1).reset_index(drop=True)
# Reading data & split into training and testing sets
X = dataset.drop(['CancerType'], 1)
#print(X)
y = dataset['CancerType']
#print(y)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.3, random_state=12345)

#Model Definition & Fitting
#clf = DecisionTreeClassifier()
clf = RandomForestClassifier(min_samples_leaf = 50, max_depth = 4)
clf = clf.fit(X_train, y_train)

# Predict based on the given features for the test set
y_pred = clf.predict(X_test)
y_pred_train = clf.predict(X_train)
#predictions_probability = clf.predict_proba(X_test)
print(y_pred)
print(y_test)

['Lung' 'Kidney' 'Blood' ... 'Blood' 'Lung' 'Breast']
1374      Lung
2673    Kidney
3956     Blood
4709     Blood
1617    Kidney
         ...  
3921      Lung
5987    Kidney
3579     Blood
4040      Lung
6157    Breast
Name: CancerType, Length: 2019, dtype: object


## Decision Tree Metrics & Plots

In [121]:
print("Train Accuracy:",metrics.accuracy_score(y_train, y_pred_train))
print("Train Precision:",metrics.precision_score(y_train, y_pred_train, average='micro'))
print("Train Recall:",metrics.recall_score(y_train, y_pred_train, average='micro'))

print("Test Accuracy:",metrics.accuracy_score(y_test, y_pred))
print("Test Precision:",metrics.precision_score(y_test, y_pred, average='micro'))
print("Test Recall:",metrics.recall_score(y_test, y_pred, average='micro'))


Train Accuracy: 0.9972393289445742
Train Precision: 0.9972393289445742
Train Recall: 0.9972393289445742
Test Accuracy: 0.9945517582961863
Test Precision: 0.9945517582961863
Test Recall: 0.9945517582961863


## Filter Features

In [122]:
imp_vals = clf.feature_importances_
print('max:',np.max(imp_vals))
print('min:',np.min(imp_vals))
print('mean:',np.mean(imp_vals))
imp_arr = imp_vals > 0
num_imp = 0
for i in imp_arr:
    if i>0:
        num_imp+=1
        
print('number of important features',num_imp)
# with np.printoptions(threshold=np.inf):
#      print(imp_vals>0)
print('bool array shape: ',imp_arr.shape)
print('dataset shape: ',X.shape)
filt_X = X.loc[:, imp_arr]
filt_X

max: 0.014769131181953445
min: 0.0
mean: 1.653357141676174e-05
number of important features 780
bool array shape:  (60483,)
dataset shape:  (6728, 60483)


ENSG00000000003.13  ENSG00000001036.12  ENSG00000001617.10  \
0               0.068400            8.151500            0.401800   
1              37.825040           22.251589            3.137434   
2               0.018900            4.651200            1.270400   
3              12.306157           12.647728           15.482653   
4              10.659837           36.011515           25.770470   
...                  ...                 ...                 ...   
6723            1.266300           18.235900            0.062200   
6724            1.915440            8.825349            0.358660   
6725            0.014800            7.425100            1.531100   
6726           24.152433           17.297232            9.696420   
6727            0.000000            9.662900            0.080500   

      ENSG00000003400.13  ENSG00000005001.8  ENSG00000005073.5  \
0               0.837200           0.000000           0.025200   
1               7.945763          10.356273           0.000000   
2               4.407000           0.018000           0.000000   
3               8.303683          48.303186           0.113600   
4               7.437456          22.025724           0.298307   
...                  ...                ...                ...   
6723           27.606300           0.009000           1.439600   
6724           10.770305           0.174569           0.097258   
6725            3.693100           0.102900           0.000000   
6726            4.106509          17.150651           0.006030   
6727            2.936200           0.006800           0.364900   

      ENSG00000005187.10  ENSG00000010295.18  ENSG00000010379.14  \
0               0.396700            3.056300            0.009100   
1               1.940665            2.152881            0.018207   
2               0.328900            4.589800            0.060600   
3               0.211611            2.287867            0.000000   
4               0.396748            1.934117            0.082628   
...                  ...                 ...                 ...   
6723            0.999900            8.047100            0.141400   
6724            8.380154           18.290806            0.060436   
6725            1.332800            1.832000            0.026300   
6726            2.502183            2.125475            0.032785   
6727           22.430200            7.393200            0.007600   

      ENSG00000010704.17  ENSG00000012504.12  ENSG00000015285.9  \
0               0.399800            0.000000          24.776500   
1               2.770157            0.022327           8.825014   
2               0.052900            0.000000          10.966100   
3               1.983345            0.003987           6.777981   
4               3.805057            0.015011           9.527267   
...                  ...                 ...                ...   
6723            0.626800            0.000000          21.994400   
6724            0.429264            0.000000          42.984908   
6725            0.062900            0.000000          50.252900   
6726            4.105742            0.012061           6.701111   
6727            0.205400            0.000000          30.924600   

      ENSG00000018280.15  ENSG00000018408.13  ENSG00000020577.12  \
0               0.194500            0.306600            1.864400   
1               3.757499            7.327535            4.157733   
2               0.909300            0.096800            0.190200   
3               2.426101            7.158248            0.516831   
4               1.652283           24.277986            0.825820   
...                  ...                 ...                 ...   
6723            0.049400            0.601100            0.596900   
6724            0.532010            0.495301            0.776977   
6725           94.641900            0.074300            0.209100   
6726            4.438020           12.630728            1.903121   
6727            0.285500  

## Decision Tree Model of Filtered Dataset

In [123]:
#Model Definition & Fitting
#clf = DecisionTreeClassifier(min_samples_leaf = 5, max_depth = 20, criterion = 'gini')
clf = RandomForestClassifier(bootstrap = True, n_estimators = 200, min_samples_leaf = 10, max_depth = 10, criterion = 'entropy')

#Cross Validation
n_folds = 4
kf = KFold(n_splits=n_folds, random_state = 54321, shuffle = True)

#Split Train/CV from Test
X_train, X_test, y_train, y_test = train_test_split(filt_X, y, test_size = 0.3, random_state=12345)

train_acc_arr = np.array([])
test_acc_arr = np.array([])
for i, (train_index, cv_index) in enumerate(kf.split(X_train)):
    X_train, X_cv = filt_X.iloc[train_index], filt_X.iloc[cv_index]
    y_train, y_cv = y.iloc[train_index], y.iloc[cv_index]
    clf = clf.fit(X_train, y_train)

    # Predict based on the given features for the test set
    y_pred_cv = clf.predict(X_cv)
    y_pred_train = clf.predict(X_train)
    #predictions_probability = clf.predict_proba(X_test)
    print('Fold #: ', i)
    print("Train Accuracy:",metrics.accuracy_score(y_train, y_pred_train))
    train_acc_arr = np.append(train_acc_arr,metrics.accuracy_score(y_train, y_pred_train))
    print("CV Accuracy:",metrics.accuracy_score(y_cv, y_pred_cv))
    test_acc_arr = np.append(test_acc_arr,metrics.accuracy_score(y_cv, y_pred_cv))
print("Avg Train Accuracy:",np.mean(train_acc_arr))
print("Avg CV Accuracy:",np.mean(test_acc_arr))

y_pred_test = clf.predict(X_test)
print("Test Accuracy:",metrics.accuracy_score(y_test, y_pred_test))
print('---Test Data---')
y_test

Fold #:  0
Train Accuracy: 0.9983007646559049
CV Accuracy: 0.9966044142614601
Fold #:  1
Train Accuracy: 0.9985843714609286
CV Accuracy: 0.9966015293118097
Fold #:  2
Train Accuracy: 0.9983012457531144
CV Accuracy: 0.9974511469838573
Fold #:  3
Train Accuracy: 0.9980181200453001
CV Accuracy: 0.9983007646559049
Avg Train Accuracy: 0.998301125478812
Avg CV Accuracy: 0.997239463803258
Test Accuracy: 0.9955423476968797
---Test Data---


1374      Lung
2673    Kidney
3956     Blood
4709     Blood
1617    Kidney
         ...  
3921      Lung
5987    Kidney
3579     Blood
4040      Lung
6157    Breast
Name: CancerType, Length: 2019, dtype: object

## Visualize Tree

In [124]:
estimator = clf.estimators_[5]

classes = np.unique(y.to_numpy())
features = filt_X.columns

from sklearn.tree import export_graphviz
# Export as dot file
export_graphviz(estimator, out_file='tree.dot', 
                feature_names = features,
                class_names = classes,
                rounded = True, proportion = False, 
                precision = 2, filled = True)

# Convert to png using system command (requires Graphviz)
from subprocess import call
call(['dot', '-Tpng', 'tree.dot', '-o', 'tree.png', '-Gdpi=600'])

# Display in jupyter notebook
from IPython.display import Image
Image(filename = 'tree.png')